In [1]:
import geopandas as gpd
import pandas as pd
import numpy as np
from unidecode import unidecode
from os.path import join

from utils import (
    save_parquet,
    download_malha_geosampa,
    _prepare_cache
)

# Declarar variáveis

In [2]:
gdf_arvore = gpd.GeoDataFrame()
gdf_distritos =  gpd.GeoDataFrame()

# Importar Dados

Este notebook é dependente dos assets reesultantes dos notebooks malha_distritos e malha_arborizacao_viaria

In [3]:
arvore_path = join('data', 'assets', 'malha_arborizacao_viaria.parquet')
gdf_arvore = gpd.read_parquet(arvore_path)

In [4]:
distritos_path = join('data', 'assets', 'distrito_ibge.parquet')
gdf_distritos = gpd.read_parquet(distritos_path)

Foi escolhido carregar a malha do IBGE, por já vir com as informações de população, ao contrário da malha do GeoSampa.

# Conferir CRS

In [5]:
gdf_arvore.crs

<Projected CRS: EPSG:31983>
Name: SIRGAS 2000 / UTM zone 23S
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Brazil - between 48°W and 42°W, northern and southern hemispheres, onshore and offshore.
- bounds: (-48.0, -33.5, -42.0, 5.13)
Coordinate Operation:
- name: UTM zone 23S
- method: Transverse Mercator
Datum: Sistema de Referencia Geocentrico para las AmericaS 2000
- Ellipsoid: GRS 1980
- Prime Meridian: Greenwich

In [6]:
gdf_distritos=gdf_distritos.to_crs(epsg='31983')
gdf_distritos.crs

<Projected CRS: EPSG:31983>
Name: SIRGAS 2000 / UTM zone 23S
Axis Info [cartesian]:
- E[east]: Easting (metre)
- N[north]: Northing (metre)
Area of Use:
- name: Brazil - between 48°W and 42°W, northern and southern hemispheres, onshore and offshore.
- bounds: (-48.0, -33.5, -42.0, 5.13)
Coordinate Operation:
- name: UTM zone 23S
- method: Transverse Mercator
Datum: Sistema de Referencia Geocentrico para las AmericaS 2000
- Ellipsoid: GRS 1980
- Prime Meridian: Greenwich

# Recortar Arborição Viária por Distrito

No gdf_arvore já tem as informações dos distritos, a partir das colunas sg_distrit e nm_distrit (respectivamente, siglas e nomes). Iremos fazer a intersecção a seguir para confirmar se há incongruências em gdf_arvore.

In [7]:
gdf_arvore_recort = gpd.overlay(gdf_arvore, gdf_distritos, 'intersection', keep_geom_type = True)

## Checar incongruências em gdf_arvore

### Verificar a quantidade de valores em cada tabela

In [8]:
print(len(gdf_arvore))

30000


In [9]:
print(len(gdf_arvore_recort))

29963


Com a malha do IBGE 18 árvores ficavam de fora, mas com esta são 37 

In [10]:
arv_faltante = (
    gdf_arvore[
        ~gdf_arvore['cd_identif']
        .isin(gdf_arvore_recort['cd_identif'])
    ]
)
arv_faltante.shape

(37, 5)

In [11]:
m_arv_falt =gdf_distritos.explore(color = 'pink', fillOpacity=0)

arv_faltante.explore(m=m_arv_falt, color = 'limegreen')

Pelo mapa podemos perceber que as árvores que não aparecem no recorte por distrito estão fora dos limites da cidade segundo as fronteiras apresentadas no gdf_distritos. Isso pode indicar uma incompatibilidade de malha, já que ambos os gdfs estão no mesmo crs.

### Incompatibilidade de distritos

Comparar sigla dos distritos em ambos os gdfs, em busca de alguma diferença.

Primeiro, vamos confirmar se há valores vazios nas colunas

In [12]:
print(f'Número de valores vazio em nm_dist_arv: {pd.isnull(gdf_arvore_recort['nm_dist_arv']).sum()}')

Número de valores vazio em nm_dist_arv: 0


In [13]:
print(f'Número de valores vazio em NM_DIST: {pd.isnull(gdf_arvore_recort['NM_DIST']).sum()}')

Número de valores vazio em NM_DIST: 0


Agora vamos ver se há difereças e quais são os casos:

In [14]:
arv_incongru = gdf_arvore_recort[gdf_arvore_recort['nm_dist_arv']!= gdf_arvore_recort['NM_DIST']]
arv_incongru.shape

(274, 22)

In [15]:
m_incongru =gdf_distritos.explore(color = 'orange', fillOpacity=0)

arv_incongru.explore(m=m_incongru, color = 'limegreen')

Com a malha do IBGE mais árvores apareceram no lugar errado (em comparação com a malha do GeoSampa, em que apenas duas árvores apareciam em distitos diferentes), contudo elas estão todas em regiões fronteiriças, que justificam essa diferença.

### Conclusão
Decidimos manter as informação do gdf_arvore, já que é a informação original, e evita assim as incongruências que se deram após a interseção dos gdfs.

# Quantidade de Árvores no Viário

## São Paulo (total)

Se cada árvore no viário corresponde a uma linha no gdf_arvore, para saber o total de árvores no município podemos ver quantas linhas têm no gdf:

In [16]:
print(f'Número de cd_identif vazios em gdf_arvore: {pd.isnull(gdf_arvore['cd_identif']).sum()}')

Número de cd_identif vazios em gdf_arvore: 0


In [17]:
print(f'Total de árvores no viário no município de São Paulo: {len(gdf_arvore)}')

Total de árvores no viário no município de São Paulo: 30000


## Por distrito

In [18]:
gdf_arvore.columns

Index(['cd_identif', 'sg_dist_arv', 'nm_dist_arv', 'nm_subpref', 'geometry'], dtype='object')

In [19]:
len(gdf_distritos)

96

Primeiro vamos ver quais os distritos que aparecem no gdf_arvore e quantas arvores no viário tem em cada um desses distritos, logo em seguida a informação da quantidade de árvores por distrito é passada para gdf_distritos.

In [20]:
uniques = gdf_arvore['nm_dist_arv'].unique()

In [21]:
for sg in uniques:
    qtd_arv = len(gdf_arvore[gdf_arvore['nm_dist_arv']==sg])
    gdf_distritos.loc[gdf_distritos['NM_DIST'] == sg, 'qtd_arv_viario'] = qtd_arv
    print(f'{sg}: {qtd_arv}')

IPIRANGA: 4046
SACOMA: 3190
CURSINO: 1319
VILA FORMOSA: 5275
CARRAO: 4256
CACHOEIRINHA: 1
LIMAO: 22
CAPAO REDONDO: 7146
VILA ANDRADE: 1148
CAMPO LIMPO: 3597


Para que não tenhamos problemas, precisamos substituir todos os espaços vazios na coluna 'qtd-arv-viario' por 0:

Como as árvores não podem ser decimais, vamos transformar o valor em inteiro 

In [22]:
gdf_distritos['qtd_arv_viario'] = (
    gdf_distritos['qtd_arv_viario']
    .fillna(0)
    .astype(int)
)

# Salvar GDF

In [23]:
data_path = join('data', 'assets')

In [24]:
save_parquet(
    gdf_distritos, 
    data_path=data_path,
    fname= 'distrito_arv_viario',
    data_subpath = 'arborizacao_viaria'
)